# Install and Defaults

In [1]:
%pip install -e ../bayes-kit
%load_ext autoreload
%autoreload 2

Obtaining file:///mnt/home/gturok/bayes-kit
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Installing backend dependencies ... done
  Preparing editable metadata (pyproject.toml) ... done
  Building editable for bayes-kit (pyproject.toml) ... done
  Created wheel for bayes-kit: filename=bayes_kit-0.0.1-0.editable-py3-none-any.whl size=4938 sha256=8d1d98b84a8a07ca471282b264d4335485bc295bedef1fd885694036dd0de02a
  Stored in directory: /tmp/pip-ephem-wheel-cache-gphps8ws/wheels/fc/9c/e4/ece1713356298681eb8ce9d05290e4466c31bbbc88586467c6
Successfully built bayes-kit
  Attempting uninstall: bayes-kit
    Found existing installation: bayes-kit 0.0.1
    Uninstalling bayes-kit-0.0.1:
      Successfully uninstalled bayes-kit-0.0.1
Note: you may need to restart the kernel to use updated packages.


In [2]:
import os
import json
from pathlib import Path
from collections import namedtuple

import numpy as np
import bridgestan as bs
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from tqdm import tqdm
from sklearn.model_selection import ParameterGrid

from posteriordb import BSDB
from utils import DualAveragingStepSize, compute_hash, my_save
from bayes_kit.drghmc import DrGhmcDiag
from bayes_kit.typing import GradModel

# Helper Functions

In [196]:
def get_model(hp):
    return BSDB(hp.model_num, hp.pdb_dir)

In [197]:
from bayes_kit import HMCDiag

def get_init_stepsize(hp):
    model = get_model(hp)
    init_stepsize = hp.first_stepsize
    dual_avg = DualAveragingStepSize(initial_step_size=init_stepsize, nadapt=hp.burn_in)
    for i in range(hp.burn_in):
        hmc = HMCDiag(model=model, steps=10, stepsize=init_stepsize)
        _, _, acceptp = hmc.sample(return_acceptp=True)
        init_stepsize = dual_avg(i=i, p_accept=acceptp)
    return init_stepsize

# Experiments

In [198]:
def sampler(sp, hp):
    model = get_model(hp)
    init_stepsize =  sp.init_stepsize
    stepsize = lambda k: init_stepsize * (sp.adaptivity_factor ** -k)
    steps = 1 if sp.leapfrog_steps == "const_num_steps" else lambda k: int(1 / stepsize(k))
    
    # remove after testing
    fname = os.path.join(hp.pdb_dir,  f'PDB_{hp.model_num:02d}', f'PDB_{hp.model_num:02d}.samples.npy') 
    init_constrained = np.load(fname)[0,-1, :].copy(order='C') # change to numpy C Contigous flag
    init = model.unconstrain(init_constrained)
    
    sampler = DrGhmcDiag(
        model=model,
        stepsize=stepsize,
        steps=steps,
        seed=hp.seed,
        init=init,
        num_proposals=sp.num_proposals,
        probabilistic=sp.probabilistic,
        dampening=sp.dampening,
    )
    
    burned_draws = np.asanyarray([sampler.sample()[0] for _ in range(hp.burn_in)])
    draws = np.asanyarray([sampler.sample()[0] for _ in range(hp.chain_length)])
    return burned_draws, draws

In [207]:
def evaluate(draws, sp, hp):
    model = get_model(hp)
    fname = os.path.join(hp.pdb_dir,  f'PDB_{hp.model_num:02d}', f'PDB_{hp.model_num:02d}.samples.npy') 
    constrained = np.load(fname)[hp.chain_num, :, :].copy(order='C') # [chain_num, n_samples, params_dim]
    reference_draws = model.unconstrain(constrained)
    
    subplot_titles = [None] * (2 * model.dims())
    subplot_titles[0] = "Reference Draws"
    subplot_titles[1] = "DrGhmc Draws"
    fig = make_subplots(rows=model.dims(), cols=2, shared_yaxes=True,
                        subplot_titles=subplot_titles,)
    
        
    for i in range(model.dims()):
        cur_ref, cur_draws = reference_draws[:, i], draws[:, i]
        
        fig.add_trace(go.Histogram(
            x=cur_ref, name=f"Reference {i+1}", 
            opacity=0.5, histnorm="probability",
        ), row=i+1, col=1)
        fig.add_annotation(
            x=np.mean(cur_ref), y=0.1, 
            text=f"μ={np.mean(cur_ref):.2f}, σ={np.std(cur_ref):.2f}",
            showarrow=False, row=i+1, col=1,)
        
        fig.add_trace(go.Histogram(
            x=draws[:, i], name=f"DrGhmc {i+1}", 
            opacity=0.5, histnorm="probability",
        ), row=i+1, col=2)
        fig.add_annotation(
            x=np.mean(cur_draws), y=0.1, 
            text=f"μ={np.mean(cur_draws):.2f}, σ={np.std(cur_draws):.2f}",
            showarrow=False, row=i+1, col=2,)
        
    sp_text = "\t".join(f"{str(k)}: {str(v)}" for k, v in sp._asdict().items())
    fig.add_annotation(xref="paper", yref="paper", text=sp_text, showarrow=False, x=0, y=-0.05) # x = 1.2, y = 0.7
    
    hp_text = "\t".join(f"{str(k)}: {str(v)}" for k, v in hp._asdict().items())
    fig.add_annotation(xref="paper", yref="paper", text=hp_text, showarrow=False, x=0, y=-0.08)
        
    fig.update_layout(height=200*model.dims(), width=1000, title_text=f"Model {hp.model_num} Chain {hp.chain_num}")
    
    
    
    return fig

In [208]:
def experiment(sp, hp):
    burned_draws, draws = sampler(sp, hp)
    fig = evaluate(draws, sp, hp)
    fig.show()
    my_save(sp, hp, burned_draws, draws, fig)
    return burned_draws, draws

In [211]:
HyperParamsTuple = namedtuple("hyper_params", ["model_num", "burn_in", "chain_length", "chain_num", "seed", "save_dir", "pdb_dir", "bridgestan_dir"])
SamplerParamsTuple = namedtuple("model_params", ["init_stepsize", "adaptivity_factor", "leapfrog_steps", "dampening", "num_proposals", "probabilistic"])

def experiment_runner(model_num, chain_num, seed):
    # although burn_in and chain_length are sampler parameters, 
    # we do not grid search over them and treat them as hyperparameters
    hp = HyperParamsTuple(
        model_num=model_num,
        burn_in=10, # initialize with reference sample, don't require real burn-in
        chain_length=5000,
        chain_num=chain_num,
        seed=seed,
        save_dir='res',
        # pdb_dir='/mnt/ceph/users/cmodi/PosteriorDB/',
        pdb_dir = '.',
        bridgestan_dir='../.bridgestan/bridgestan-2.1.1/',
    )
    
    sampler_param_grid = ParameterGrid(
        {"init_stepsize": [1e-3],
        "adaptivity_factor": [2],
        "leapfrog_steps": ["const_num_steps", "const_trajectory_length"],
        "dampening": [0.05],
        "num_proposals": [3],
        "probabilistic": [True, False]}
    )

    bs.set_bridgestan_path(hp.bridgestan_dir)
    for sampler_params in tqdm(sampler_param_grid):
        sp = SamplerParamsTuple(**sampler_params)
        experiment(sp, hp)

In [212]:
model_num = 1
chain_num = 0
seed = 0

experiment_runner(model_num, chain_num, seed)

  0%|          | 0/4 [00:00<?, ?it/s]

 25%|██▌       | 1/4 [00:05<00:16,  5.63s/it]

 50%|█████     | 2/4 [00:15<00:16,  8.26s/it]

 75%|███████▌  | 3/4 [13:49<06:16, 376.01s/it]

100%|██████████| 4/4 [27:42<00:00, 415.71s/it]
